Dans ce TP, nous allons entraîner et tester un RNN pour la génération de texte. Plus précisément, le modèle que nous allons construire sera capable, étant donnée une séquence de caractères, de prédire le prochain caractère le plus probable.

![model](https://drive.google.com/uc?id=1syE1phix6Pu-b8y9ktol0thCdC2lzmlV
)

Il sera alors possible, partant d'une chaîne de caractères, de réaliser plus inférences successivement du modèle pour générer la suite de la phrase.

![inference](https://drive.google.com/uc?id=1T6J3UgFV4Q2JhJm3984HhJIkH7ukWkb7
)

Les phrases suivantes ont été obtenues à l'issue d'un entraînement du modèle sur une base de données regroupant les tweets de Donald Trump (à partir respectivement des débuts de phrase 'China', 'Obama', et 'Mo'). Même si les phrases ne sont pas complètement correctes, le modèle arrive à générer des mots existants (pour la plupart) et à les enchaîner d'une manière tout de même relativement crédible !



<pre>
China on dollars are sources to other things!The Fake News State approvement is smart, restlected & unfair 

Obama BEAT!Not too late. This is the only requirement. Also, the Fake News is running a big democrats want 

More system. See you really weak!Thank you. You and others just doesn’t exist.
</pre>

Le reste du notebook a été adapté du tutorial https://www.tensorflow.org/text/tutorials/text_generation. Il n'y aura pas de code à compléter, l'objectif du TP est de découvrir comment préparer la base de données, implémenter et entraîner le modèle, et réaliser l'inférence.

A vous de vous emparer du code ci-dessous pour essayer d'améliorer les performances du modèle et de générer les phrases les plus crédibles possibles ! 

# Téléchargement des données

In [ ]:
import tensorflow as tf

import numpy as np
import os
import time

Téléchargement des données

In [ ]:
path_to_file = tf.keras.utils.get_file('realdonaltrump.csv', 'https://drive.google.com/uc?export=download&id=1s1isv9TQjGiEr2gG__8bOdBFvQlmepRt')

On commence par extraire les tweets du CSV (notez qu'il y a d'autres métadonnées dans le fichier, comme le nombre de retweets par exemple, qui pourraient être utilisées pour d'autres tâches).

In [ ]:
import csv
tweets = []
text = ''
with open(path_to_file, newline='') as csvfile:
    reader = csv.DictReader(csvfile)
    for row in reader:
        tweets.append(row['content'])
        text += row['content']

# Affichage des 10 premiers tweets
print(tweets[:10])

In [ ]:
# Nombre total de caractères du dataset
print(f'Longueur totale du texte: {len(text)} caractères')

In [ ]:
# Extraction des caractères uniques du texte
vocab = sorted(set(text))
print(f'{len(vocab)} unique caractères')

In [ ]:
# Affichage du vocabulaire
print(vocab)

# Préparation des données

Il est nécessaire de convertir les caractères dans une représentation admissible par le modèle. 

La fonction `tf.keras.layers.StringLookup` convertit les chaînes de caractères en nombre, en reprenant l'indice de chaque caractère dans le vocabulaire établi précédemment.

Il faut cependant commencer par séparer le texte en caractères, comme présenté sur l'exemple ci-dessous.

In [ ]:
example_texts = ['abcdefg', 'xyz']

chars = tf.strings.unicode_split(example_texts, input_encoding='UTF-8')
chars

On peut ensuire appliquer la fonction `tf.keras.layers.StringLookup` :

In [ ]:
ids_from_chars = tf.keras.layers.StringLookup(
    vocabulary=list(vocab), mask_token=None)

In [ ]:
ids = ids_from_chars(chars)
ids

Pour retrouver un texte à partir de sa représentation numérique (ce sera utile lors de l'étape finale de génération) il faut être capable d'inverser le processus, ce que l'on peut faire avec `tf.keras.layers.StringLookup(..., invert=True)`.  

In [ ]:
chars_from_ids = tf.keras.layers.StringLookup(
    vocabulary=ids_from_chars.get_vocabulary(), invert=True, mask_token=None)

In [ ]:
chars = chars_from_ids(ids)
chars

Enfin, on peut recréer une chaîne de caractères :

In [ ]:
tf.strings.reduce_join(chars, axis=-1).numpy()

In [ ]:
def text_from_ids(ids):
  return tf.strings.reduce_join(chars_from_ids(ids), axis=-1)

Il faut maintenant créer les exemples d'apprentissage, ainsi que leurs labels associés. Pour cela, nous allons diviser le texte en séquences, chacune composée de `seq_length` caractères.

Pour chaque séquence constituant un ensemble d'apprentissage, le label à prédire correspondant est une séquence de même longueur dont tous les caractères ont été décalés d'un cran. 

Une manière simple de constituer notre base est donc de diviser le texte en séquences de longueur `seq_length+1`, et d'utiliser les `seq_length` premiers caractères comme donnée, et les `seq_length` derniers caractères comme label.


N.B. Cette manière de faire n'est clairement pas optimale ! Certaines séquences vont recouvrir deux tweets successifs, qui n'auront potentiellement aucun lien entre eux !

In [ ]:
all_ids = ids_from_chars(tf.strings.unicode_split(text, 'UTF-8'))
all_ids

In [ ]:
ids_dataset = tf.data.Dataset.from_tensor_slices(all_ids)

In [ ]:
for ids in ids_dataset.take(10):
    print(chars_from_ids(ids).numpy().decode('utf-8'))

In [ ]:
seq_length = 50


La méthode `batch` permet de regrouper les caractères du texte en séquences de la longueur voulue.

In [ ]:
sequences = ids_dataset.batch(seq_length+1, drop_remainder=True)

for seq in sequences.take(1):
  print(chars_from_ids(seq))

Voici par exemple les premières séquences extraites du dataset :

In [ ]:
for seq in sequences.take(5):
  print(text_from_ids(seq).numpy())

Nous allons maintenant générer les couples (données, labels) à partir des séquences extraites :

In [ ]:
def split_input_target(sequence):
    input_text = sequence[:-1]
    target_text = sequence[1:]
    return input_text, target_text

In [ ]:
split_input_target(list("Tensorflow"))

In [ ]:
dataset = sequences.map(split_input_target)

In [ ]:
for input_example, target_example in dataset.take(1):
    print("Input :", text_from_ids(input_example).numpy())
    print("Target:", text_from_ids(target_example).numpy())

Avant de pouvoir fournir les données au modèle, il est important de les ranger dans un ordre aléatoire et de les regrouper en batches.

Le paramètre `prefetch` permet d'organiser le chargement du prochain batch de données pendant que le modèle est en train de traiter le précédent.

In [ ]:
# Batch size
BATCH_SIZE = 64

# Buffer size to shuffle the dataset
# (TF data is designed to work with possibly infinite sequences,
# so it doesn't attempt to shuffle the entire sequence in memory. Instead,
# it maintains a buffer in which it shuffles elements).
BUFFER_SIZE = 10000

dataset = (
    dataset
    .shuffle(BUFFER_SIZE)
    .batch(BATCH_SIZE, drop_remainder=True)
    .prefetch(tf.data.experimental.AUTOTUNE))

dataset

# Construction du modèle

Le modèle sera composé de 3 couches seulement :

* `tf.keras.layers.Embedding`: La couche d'entrée, qui permet d'apprendre un descripteur de dimension`embedding_dim` à associer à chacun des caractères passés en entrée;
* `tf.keras.layers.GRU`: Une cellule récurrente, avec `rnn_units` neurones (que l'on pourrait tout à fait remplacer par un LSTM)
* `tf.keras.layers.Dense`: La couche de sortie, avec `vocab_size` neurones. Notez qu'on ne spécifie pas la fonction d'activation (`softmax`) car elle est intégrée directement dans la fonction de coût.

In [ ]:
# Taille du vocabulaire
vocab_size = len(ids_from_chars.get_vocabulary())

# Dimension des descripteurs de caractères
embedding_dim = 256

# Nombre de neurones du GRU
rnn_units = 512

In [ ]:
class MyModel(tf.keras.Model):
  def __init__(self, vocab_size, embedding_dim, rnn_units):
    super().__init__(self)
    self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
    self.gru = tf.keras.layers.GRU(rnn_units,
                                   return_sequences=True,
                                   return_state=True)
    self.dense = tf.keras.layers.Dense(vocab_size)

  def call(self, inputs, states=None, return_state=False, training=False):
    x = inputs
    x = self.embedding(x, training=training)
    if states is None:
      states = self.gru.get_initial_state(x)
    x, states = self.gru(x, initial_state=states, training=training)
    x = self.dense(x, training=training)

    if return_state:
      return x, states
    else:
      return x

N.B. Cette manière inhabituelle de définir le modèle (qui ressemble d'ailleurs beaucoup au formalisme Pytorch) est utile pour l'inférence. Nous aurions pu utiliser un modèle classique (construit avec `keras.Sequential`) mais cela ne nous aurait pas donné d'accès simple aux états internes du GRU. Il sera important de pouvoir manipuler cet état lorsque nous enchaînerons plusieurs prédictions successives, qui nécessiteront chaque fois de repartir de l'état obtenu lors de la prédiction précédente. Cette opération n'est pas possible avec le modèle Sequentiel que nous utilisons d'habitude.

In [ ]:
model = MyModel(
    vocab_size=vocab_size,
    embedding_dim=embedding_dim,
    rnn_units=rnn_units)

Pour chaque caractère de la séquence, le modèle produit le descripteur associé, applique un pas de temps du GRU et enfin applique la couche dense pour obtenir la prédiction du réseau :

![A drawing of the data passing through the model](https://drive.google.com/uc?id=1GYD8U9aF-MTC1XpJ3VKpY1b0clJuO4wb)

Nous pouvons tester notre modèle sur le premier exemple d'apprentissage, pour vérifier les dimensions :

In [ ]:
for input_example_batch, target_example_batch in dataset.take(1):
    example_batch_predictions = model(input_example_batch)
    print(example_batch_predictions.shape, "# (batch_size, sequence_length, vocab_size)")

In [ ]:
model.summary()

# Entraînement du modèle

Le problème que nous cherchons à résoudre est celui d'une classification à `vocab_size` classes.

On utilise la fonction de coût `tf.keras.losses.sparse_categorical_crossentropy` car nos labels sont sous forme d'indices (et pas de *one-hot vectors*). Le flag `from_logits` positionné à `True` indique qu'il faut au préalable appliquer la fonction softmax à la sortie du réseau.

In [ ]:
model.compile(optimizer='adam', loss = tf.losses.SparseCategoricalCrossentropy(from_logits=True))

In [ ]:
history = model.fit(dataset, epochs=5)

# Génération de texte

Pour générer un texte, il suffit de partir d'une séquence initiale, d'effectuer une prédiction, et de conserver l'état interne du modèle pour pouvoir le restaurer lors de la prochaine inférence, qui prendra en entrée la séquence initiale augmentée du caractère prédit précédemment.


La classe suivante permet de réaliser une prédiction :

In [ ]:
class OneStep(tf.keras.Model):
  def __init__(self, model, chars_from_ids, ids_from_chars, temperature=1):
    super().__init__()
    self.temperature = temperature
    self.model = model
    self.chars_from_ids = chars_from_ids
    self.ids_from_chars = ids_from_chars


  @tf.function
  def generate_one_step(self, inputs, states=None):
    # Convert strings to token IDs.
    input_chars = tf.strings.unicode_split(inputs, 'UTF-8')
    input_ids = self.ids_from_chars(input_chars).to_tensor()

    # Run the model.
    # predicted_logits.shape is [batch, char, next_char_logits]
    predicted_logits, states = self.model(inputs=input_ids, states=states,
                                          return_state=True)
    # Only use the last prediction.
    predicted_logits = predicted_logits[:, -1, :]
    predicted_logits = predicted_logits/self.temperature

    # Sample the output logits to generate token IDs.
    predicted_ids = tf.random.categorical(predicted_logits, num_samples=1)
    predicted_ids = tf.squeeze(predicted_ids, axis=-1)

    # Convert from token ids to characters
    predicted_chars = self.chars_from_ids(predicted_ids)

    # Return the characters and model state.
    return predicted_chars, states

In [ ]:
one_step_model = OneStep(model, chars_from_ids, ids_from_chars)

Il reste à appeler cette fonction dans une boucle opour générer un texte complet :

In [ ]:
start = time.time()
states = None
next_char = tf.constant(['Obama '])
result = [next_char]

for n in range(100):
  next_char, states = one_step_model.generate_one_step(next_char, states=states)
  result.append(next_char)

result = tf.strings.join(result)
end = time.time()
print(result[0].numpy().decode('utf-8'), '\n\n' + '_'*80)
print('\nRun time:', end - start)

A vous de jouer pour améliorer les résultats. Vous pouvez par exemple :      
- Jouer avec le paramètre de température dans la classe `OneStep` pour accentuer ou diminuer le caractère aléatoire des prédictions.
- Modifier le réseau en rajoutant des couches supplémentaires, ou en modifiant le nombre de neurones de la couche GRU.
- Modifier la préparation des données pour éviter le problème des séquences chevauchant plusieurs tweets
- Entraîner le modèle plus longtemps devrait également aider !